In [1]:
import os
import json
import pandas as pd
import numpy as np
import plotly.express as px
import seaborn as sns
import matplotlib.pyplot as plt

In [2]:
df = pd.read_csv('merged_books.csv')
df.head(2)

Unnamed: 0                                           Название  \
0       35657  Наблюдая за китами. Прошлое, настоящее и будущ...   
1       52263  Параллельные миры: Об устройстве мироздания, в...   

          Автор Рейтинг               ISBN Год издания       Издательство  \
0  Ник Пайенсон     4,1  978-5-91671-995-6        2020  Альпина нон-фикшн   
1    Митио Каку     4,4  978-5-91671-785-3        2022  Альпина нон-фикшн   

  Прочитали Рецензии                                           Описание  \
0       225       28  Книга рассказывает о прошлом, настоящем и буду...   
1       353       14  Если в конечном итоге нашей Вселенной суждено ...   

                 Жанр  price (rub)  
0  Природа и животные        827.0  
1              Физика        735.0

In [3]:
df.drop(columns=['Unnamed: 0'], inplace=True)

In [4]:
df.drop_duplicates(inplace=True)

In [5]:
df.dtypes

Название         object
Автор            object
Рейтинг          object
ISBN             object
Год издания      object
Издательство     object
Прочитали        object
Рецензии         object
Описание         object
Жанр             object
price (rub)     float64
dtype: object

In [6]:
df['Прочитали'] = df['Прочитали'].apply(lambda x: x.replace('K', '000'))

In [7]:
df['Рейтинг'] = df['Рейтинг'].apply(lambda x: x.replace(',', '.'))

In [8]:
df['Рецензии'] = df['Рецензии'].apply(lambda x: x.replace('Не найдено', 'Nan'))

In [9]:
df['Год издания'] = pd.to_numeric(df['Год издания'], errors='coerce')
df['Прочитали'] = pd.to_numeric(df['Прочитали'], errors='coerce')
df['Рецензии'] = pd.to_numeric(df['Рецензии'], errors='coerce')
df['Рейтинг'] = pd.to_numeric(df['Рейтинг'], errors='coerce')
df['Год издания'] = pd.to_numeric(df['Год издания'], errors='coerce').astype('Int64')
df.dtypes

Название         object
Автор            object
Рейтинг         float64
ISBN             object
Год издания       Int64
Издательство     object
Прочитали       float64
Рецензии        float64
Описание         object
Жанр             object
price (rub)     float64
dtype: object

In [10]:
df.isnull().sum()

Название           0
Автор              0
Рейтинг            0
ISBN               0
Год издания      319
Издательство       0
Прочитали        126
Рецензии        2413
Описание           2
Жанр               0
price (rub)       26
dtype: int64

In [11]:
num_columns = ['Рейтинг', 'Год издания', 'Прочитали', 'Рецензии', 'price (rub)']

In [12]:
df[num_columns].corr()

Рейтинг  Год издания  Прочитали  Рецензии  price (rub)
Рейтинг      1.000000     0.026776   0.066775  0.150746     0.004051
Год издания  0.026776     1.000000   0.174598  0.188241     0.005058
Прочитали    0.066775     0.174598   1.000000  0.702490    -0.015243
Рецензии     0.150746     0.188241   0.702490  1.000000    -0.013399
price (rub)  0.004051     0.005058  -0.015243 -0.013399     1.000000

In [13]:
df.columns

Index(['Название', 'Автор', 'Рейтинг', 'ISBN', 'Год издания', 'Издательство',
       'Прочитали', 'Рецензии', 'Описание', 'Жанр', 'price (rub)'],
      dtype='object')

In [14]:
fig = px.histogram(df, x='Рейтинг', nbins=10, title='Распределение рейтингов по книгам',
                   labels={'Рейтинг': 'Рейтинг', 'count': 'Количество книг'})
fig.show()

In [15]:
fig = px.scatter(df, x='Рецензии', y='Рейтинг', title='Корреляция рейтинга с числом рецензий',
                 labels={'Рецензии': 'Число рецензий', 'Рейтинг': 'Рейтинг'},
                 trendline='ols')
fig.show()

correlation = df['Рейтинг'].corr(df['Рецензии'])
print(f"Коэффициент корреляции между рейтингом и числом рецензий: {correlation:.2f}")

Коэффициент корреляции между рейтингом и числом рецензий: 0.15


In [20]:
high_rating_threshold = 4.5
low_reviews_threshold = 10

high_rating_low_reviews = df[
    (df['Рейтинг'] >= high_rating_threshold) &
    (df['Рецензии'] <= low_reviews_threshold)
]
fig = px.scatter(df, x='Рецензии', y='Рейтинг', title='Книги с высоким рейтингом и малым числом рецензий',
                 labels={'Рецензии': 'Число рецензий', 'Рейтинг': 'Рейтинг'},
                 hover_data=['Название', 'Автор'])

fig.add_scatter(x=high_rating_low_reviews['Рецензии'], y=high_rating_low_reviews['Рейтинг'],
                mode='markers', marker=dict(color='red', size=10),
                name='Высокий рейтинг, мало рецензий')

fig.show()

print("Книги с высоким рейтингом, но малым числом рецензий:")
print(high_rating_low_reviews[['Название', 'Автор', 'Рейтинг', 'Рецензии']][:10])

Книги с высоким рейтингом, но малым числом рецензий:
                                              Название                 Автор  \
16   Motley Crue. Грязь. История самой скандальной ...             Mick Mars   
20   Великие тайны океанов. Атлантический океан. Ин...             Жорж Блон   
51          «...я прожил жизнь». Письма. 1920-1950 гг.       Андрей Платонов   
62                                     Бетонное казино        Сергей Смирнов   
67                   Цивилизация средневекового запада           Жак Ле Гофф   
82   Мир-система Модерна. Том 4. Триумф центристско...  Иммануил Валлерстайн   
95                Я был на этой войне. Чечня, год 1995      Вячеслав Миронов   
96                              Волшебные искры солнца            Анна Джейн   
123         Романовы. Моя первая книга о русских царях    Валентина Летунова   
135                        500 фильмов, изменивших мир            Не найдено   

     Рейтинг  Рецензии  
16       4.6       3.0  
20       4.6    

In [24]:

high_rating_threshold = 4.5
low_reviews_threshold = 10

df['Категория'] = 'Средний рейтинг, среднее число рецензий'
df.loc[(df['Рейтинг'] >= high_rating_threshold) & (df['Рецензии'] <= low_reviews_threshold), 'Категория'] = 'Высокий рейтинг, мало рецензий'
df.loc[(df['Рейтинг'] >= high_rating_threshold) & (df['Рецензии'] > low_reviews_threshold), 'Категория'] = 'Высокий рейтинг, много рецензий'
df.loc[(df['Рейтинг'] < high_rating_threshold) & (df['Рецензии'] <= low_reviews_threshold), 'Категория'] = 'Низкий рейтинг, мало рецензий'
df.loc[(df['Рейтинг'] < high_rating_threshold) & (df['Рецензии'] > low_reviews_threshold), 'Категория'] = 'Низкий рейтинг, много рецензий'

fig = px.scatter(df, x='Рецензии', y='Рейтинг', title='Группировка книг по рейтингу и числу рецензий',
                 labels={'Рецензии': 'Число рецензий', 'Рейтинг': 'Рейтинг'},
                 hover_data=['Название', 'Автор'],
                 color='Категория',
                 size='Рецензии')
fig.show()

In [22]:
df['Рецензии'] = pd.to_numeric(df['Рецензии'], errors='coerce')

df['Рецензии'] = df['Рецензии'].fillna(0)

print(df['Рецензии'].isna().sum())

fig = px.scatter(df, x='Рецензии', y='Рейтинг', title='Группировка книг по рейтингу и числу рецензий',
                 labels={'Рецензии': 'Число рецензий', 'Рейтинг': 'Рейтинг'},
                 hover_data=['Название', 'Автор'],
                 color='Рейтинг',
                 size='Рецензии',
                 color_continuous_scale='viridis')
fig.show()

0


In [25]:
top_100_books = df.sort_values(by='Рейтинг', ascending=False).head(100)

price_stats = top_100_books['price (rub)'].describe()
print("Описательная статистика цен для топ-100 книг:")
print(price_stats)

fig = px.histogram(top_100_books, x='price (rub)', nbins=20,
                   title='Распределение цен для топ-100 книг по рейтингу',
                   labels={'price (rub)': 'Цена (руб)', 'count': 'Количество книг'},
                   color_discrete_sequence=['blue'])
fig.show()

Описательная статистика цен для топ-100 книг:
count     100.000000
mean      532.480000
std       435.001857
min        77.000000
25%       284.000000
50%       475.500000
75%       650.000000
max      2917.000000
Name: price (rub), dtype: float64


In [27]:
import pandas as pd
import plotly.express as px


genre_counts = df['Жанр'].value_counts().reset_index()
genre_counts.columns = ['Жанр', 'Количество книг']

genre_counts = genre_counts.sort_values(by='Количество книг', ascending=True)

top_20_genres = genre_counts.tail(20)

fig = px.bar(top_20_genres, y='Жанр', x='Количество книг',
             title='Топ-20 жанров по количеству книг (от меньшего к большему)',
             labels={'Жанр': 'Жанр', 'Количество книг': 'Количество книг'},
             text='Количество книг',
             orientation='h')

fig.update_traces(textposition='outside', marker_color='skyblue')
fig.update_layout(xaxis_title='Количество книг', yaxis_title='Жанр',
                  template='plotly_white',
                  yaxis={'categoryorder': 'total ascending'})

fig.show()

In [28]:
genre_reviews = df.groupby('Жанр')['Рецензии'].sum().reset_index()

genre_reviews = genre_reviews.sort_values(by='Рецензии', ascending=False)

top_n_genres = genre_reviews.head(20)

fig = px.bar(top_n_genres, y='Жанр', x='Рецензии',
             title='Топ-20 жанров по количеству рецензий',
             labels={'Жанр': 'Жанр', 'Рецензии': 'Количество рецензий'},
             text='Рецензии',
             orientation='h')
fig.update_traces(textposition='outside', marker_color='skyblue')
fig.update_layout(xaxis_title='Количество рецензий', yaxis_title='Жанр',
                  template='plotly_white',
                  yaxis={'categoryorder': 'total descending'})

fig.show()

In [29]:
author_counts = df['Автор'].value_counts().reset_index().head(10)
author_counts.columns = ['Автор', 'Количество книг']
fig = px.bar(author_counts, y='Автор', x='Количество книг',
             title='Топ-10 авторов по количеству книг',
             labels={'Автор': 'Автор', 'Количество книг': 'Количество книг'},
             orientation='h')
fig.show()

In [30]:
fig = px.scatter(df, x='Год издания', y='Рейтинг',
                 title='Зависимость рейтинга от года издания',
                 trendline='ols',  # Линия тренда
                 labels={'Год издания': 'Год издания', 'Рейтинг': 'Рейтинг'})
fig.show()

In [31]:
fig = px.histogram(df, x='Год издания', nbins=30,
                   title='Распределение книг по годам издания',
                   labels={'Год издания': 'Год издания', 'count': 'Количество книг'})
fig.show()

In [33]:
publisher_counts = df['Издательство'].value_counts().reset_index().head(10)
publisher_counts.columns = ['Издательство', 'Количество книг']
fig = px.bar(publisher_counts, x='Издательство', y='Количество книг',
             title='Распределение книг по издательствам',
             labels={'Издательство': 'Издательство', 'Количество книг': 'Количество книг'})
fig.show()

In [38]:
fig = px.bar(top_20_books, x='Название', y='Рейтинг',
             title='Топ-20 книг по рейтингу с рецензиями > 50',
             labels={'Название': 'Название книги', 'Рейтинг': 'Рейтинг'},
             text='Рецензии',
             hover_data=['Автор'])

fig.update_traces(textposition='outside', marker_color='skyblue')
fig.update_layout(xaxis_title='Название книги', yaxis_title='Рейтинг',
                  template='plotly_white')

fig.show()